<a href="https://colab.research.google.com/github/won195/TIL/blob/master/folium.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [17]:
!pip install pyproj

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [18]:
import pandas as pd
from pyproj import Proj, transform
import folium
from folium.plugins import MarkerCluster


In [19]:
df1 = pd.read_csv('/content/drive/MyDrive/상권분석/서울시 우리마을가게 상권분석서비스(상권영역).csv', encoding='cp949')

In [20]:
df1['상권_구분_코드_명'].unique()

array(['골목상권', '발달상권', '전통시장', '관광특구'], dtype=object)

In [25]:
df2 = df1[df1['상권_구분_코드_명']=='골목상권']
df3 = df1[df1['상권_구분_코드_명']=='발달상권']
df4 = df1[df1['상권_구분_코드_명']=='전통시장']
df5 = df1[df1['상권_구분_코드_명']=='관광특구']

In [26]:


# EPSG 5181 좌표계
proj_epsg5181 = Proj(init='epsg:5181')

# WGS84 좌표계
proj_wgs84 = Proj(init='epsg:4326')

# 새로운 컬럼 생성
df1['lat'] = 0.0
df1['long'] = 0.0

# 좌표 변환
for i, row in df1.iterrows():
    x = row['엑스좌표_값']
    y = row['와이좌표_값']
    lat, long = transform(proj_epsg5181, proj_wgs84, x, y)
    df1.at[i, 'lat'] = lat
    df1.at[i, 'long'] = long


/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)
<ipython-input-26-67d2dade6dfa>:15: FutureWarning: This function is deprecated. See: https://pyproj4.github.io/pyproj/stable/gotchas.html#upgrading-to-pyproj-2-from-pyproj-1
  lat, long = transform(proj_epsg5181, proj_wgs84, x

In [29]:
df2 = df1[df1['상권_구분_코드_명']=='골목상권']
df3 = df1[df1['상권_구분_코드_명']=='발달상권']
df4 = df1[df1['상권_구분_코드_명']=='전통시장']
df5 = df1[df1['상권_구분_코드_명']=='관광특구']

In [30]:
df2

기준_년월_코드 상권_구분_코드 상권_구분_코드_명    상권_코드             상권_코드_명  엑스좌표_값  \
0       202112        A       골목상권  2110753         시흥동 은행나무사거리  191934   
1       202112        A       골목상권  2110427          노원 을지대학교병원  206265   
2       202112        A       골목상권  2110755            동일여자고등학교  192300   
3       202112        A       골목상권  2110739          시흥3동 우편취급국  191289   
4       202112        A       골목상권  2111017            송파나루역 3번  210222   
...        ...      ...        ...      ...                 ...     ...   
1085    202112        A       골목상권  2110881    구립대학경로당(관악산샘말공원)  194346   
1086    202112        A       골목상권  2110874   원신초등학교(구세군관악영문교회)  193876   
1087    202112        A       골목상권  2110887  서울산업정보학교(서울삼성초등학교)  194791   
1088    202112        A       골목상권  2110944     서울나래학교(염곡어린이공원)  204541   
1089    202112        A       골목상권  2110870     신림주공2단지(광신고등학교)  193498   

      와이좌표_값  시군구_코드    행정동_코드  형태정보         lat       long  
0     438813   11545  11545710   NaN  126.908844  37.448687  
1     459431   11350  11350611   NaN  127.070978  37.634469  
2     439070   11545  11545680   NaN  126.912978  37.451006  
3     438014   11545  11545690   NaN  126.901564  37.441482  
4     445516   11710  11710562   NaN  127.115614  37.509060  
...      ...     ...       ...   ...         ...        ...  
1085  440875   11620  11620735   NaN  126.936087  37.467284  
1086  440959   11620  11620745   NaN  126.930773  37.468038  
1087  441118   11620  11620735   NaN  126.941116  37.469476  
1088  440378   11650  11650660   NaN  127.051329  37.462812  
1089  440459   11620  11620745   NaN  126.926505  37.463530  

[1090 rows x 12 columns]

#전체

In [31]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=2000,
    height=1000,

)
for _, row in df1.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(m)


m

In [32]:
import requests
import json

# 서울 행정구역 json raw파일(githubcontent)
r = requests.get('https://raw.githubusercontent.com/southkorea/seoul-maps/master/kostat/2013/json/seoul_municipalities_geo_simple.json')
c = r.content
seoul_geo = json.loads(c)

In [33]:
# (1) 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df1.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [34]:
# (1) 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df1.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [35]:
m = folium.Map(
    location=[37.559819, 126.963895],
    zoom_start=11, 
    tiles='cartodbpositron'
)



marker_cluster = MarkerCluster().add_to(m)

for _, row in df1.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)

m


# 골목상권

In [36]:
df2

기준_년월_코드 상권_구분_코드 상권_구분_코드_명    상권_코드             상권_코드_명  엑스좌표_값  \
0       202112        A       골목상권  2110753         시흥동 은행나무사거리  191934   
1       202112        A       골목상권  2110427          노원 을지대학교병원  206265   
2       202112        A       골목상권  2110755            동일여자고등학교  192300   
3       202112        A       골목상권  2110739          시흥3동 우편취급국  191289   
4       202112        A       골목상권  2111017            송파나루역 3번  210222   
...        ...      ...        ...      ...                 ...     ...   
1085    202112        A       골목상권  2110881    구립대학경로당(관악산샘말공원)  194346   
1086    202112        A       골목상권  2110874   원신초등학교(구세군관악영문교회)  193876   
1087    202112        A       골목상권  2110887  서울산업정보학교(서울삼성초등학교)  194791   
1088    202112        A       골목상권  2110944     서울나래학교(염곡어린이공원)  204541   
1089    202112        A       골목상권  2110870     신림주공2단지(광신고등학교)  193498   

      와이좌표_값  시군구_코드    행정동_코드  형태정보         lat       long  
0     438813   11545  11545710   NaN  126.908844  37.448687  
1     459431   11350  11350611   NaN  127.070978  37.634469  
2     439070   11545  11545680   NaN  126.912978  37.451006  
3     438014   11545  11545690   NaN  126.901564  37.441482  
4     445516   11710  11710562   NaN  127.115614  37.509060  
...      ...     ...       ...   ...         ...        ...  
1085  440875   11620  11620735   NaN  126.936087  37.467284  
1086  440959   11620  11620745   NaN  126.930773  37.468038  
1087  441118   11620  11620735   NaN  126.941116  37.469476  
1088  440378   11650  11650660   NaN  127.051329  37.462812  
1089  440459   11620  11620745   NaN  126.926505  37.463530  

[1090 rows x 12 columns]

In [37]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=2000,
    height=1000,
)

for _, row in df2.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(m)

m

In [38]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df2.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [39]:
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df2.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [40]:
m = folium.Map(
    location=[37.559819, 126.963895],
    zoom_start=11, 
    tiles='cartodbpositron'
)



marker_cluster = MarkerCluster().add_to(m)

for _, row in df2.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)

m


# 발달상권

In [41]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=2000,
    height=1000,
)

for _, row in df3.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(m)

m

In [42]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df3.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [43]:
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df3.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [44]:
m = folium.Map(
    location=[37.559819, 126.963895],
    zoom_start=11, 
    tiles='cartodbpositron'
)



marker_cluster = MarkerCluster().add_to(m)

for _, row in df3.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)

m


# 전통시장

In [45]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=2000,
    height=1000,
)

for _, row in df4.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(m)

m

In [46]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df4.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [47]:
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df4.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [48]:
m = folium.Map(
    location=[37.559819, 126.963895],
    zoom_start=11, 
    tiles='cartodbpositron'
)



marker_cluster = MarkerCluster().add_to(m)

for _, row in df4.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)

m


# 관광특구

In [49]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=2000,
    height=1000,
)

for _, row in df5.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(m)

m

In [50]:
# 지도 생성
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df5.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [51]:
m = folium.Map(
    location=[37.56667, 126.97806], # 서울
    zoom_start=13,
    width=1300,
    height=800,

)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)


marker_cluster = MarkerCluster().add_to(m)

for _, row in df5.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)


m

In [52]:
m = folium.Map(
    location=[37.559819, 126.963895],
    zoom_start=11, 
    tiles='cartodbpositron'
)



marker_cluster = MarkerCluster().add_to(m)

for _, row in df5.iterrows():
    folium.Marker(location=[row['long'], row['lat']]).add_to(marker_cluster)

folium.GeoJson(
    seoul_geo,
    name='지역구'
).add_to(m)

m


https://teddylee777.github.io/visualization/folium/